PROJECT: VISUALIZATION OF ACCIDENTS IN NY.

SUBPROJECT: Creation of Map with Markers Based on # Accidents in NY

At this subproject I'll try to create map of Manhattan NYC with markers in Folium by showing places of fatal and non-fatal accidents using data from https://data.cityofnewyork.us/NYC-BigApps/NYPD-Motor-Vehicle-Collisions-Summary/m666-sf2m

First of all we download necessary libraries to Jupyter notebook

In [6]:
import pandas as pd
import folium
from folium.features import CustomIcon
from folium.plugins import MarkerCluster
from folium.plugins import FastMarkerCluster
from folium.plugins import HeatMap

We will use stats from NYPD about Motor Vehicle Collisions. Link is provided in the description section.

In [7]:
df = pd.read_csv(r'C:\Users\Mi Notebook\Downloads\NYPD_Motor_Vehicle_Collisions.csv', parse_dates = ['DATE', 'TIME'])

C:\Users\Mi Notebook\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:2785: DtypeWarning: Columns (3) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


This data contain all collisions stats starting from 2012 and has 1385920 rows therefore for this project we will use stats only for 2018.

In [8]:
df18 = df[(df['DATE']>='2018-01-01') & (df['DATE']<'2018-11-01')]

Then we do some cleaning of data that contain missing values and leaving only data with fatal accidents and acccidents with injuries

In [9]:
df18.dropna(how = 'all', inplace=True)
df18.dropna(subset=['LATITUDE', 'LONGITUDE'], how = 'any', inplace=True)
df18.dropna(subset=['NUMBER OF PERSONS INJURED', 'NUMBER OF PERSONS KILLED'], how = 'any', inplace=True)

C:\Users\Mi Notebook\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.
C:\Users\Mi Notebook\Anaconda3\lib\site-packages\ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
C:\Users\Mi Notebook\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  This is separate from the ipykernel package so we can avoid doing imports until


In [10]:
df18_flags = df18[(df18['NUMBER OF PERSONS INJURED']!=0) | (df18['NUMBER OF PERSONS KILLED']!=0)]

Now we can choose Manhattan borough for visualisation .

In [12]:
df18_flag_man = df18_flags[df18_flags['BOROUGH']=='MANHATTAN']

In [14]:
df18_flag_man.reset_index(inplace = True)

We will have three kind of markers depending whether pedestrains, cyclist or drivers participated in an accident and two colors: red if an accident was fatal or blue if there were injuries. We create three functions that set color, set icon and describe accident.

In [15]:
# This function will add column with colors in the dataframe
def set_color(row):
    if row['NUMBER OF PERSONS INJURED'] > 0:
        return 'blue'
    elif row['NUMBER OF PERSONS KILLED'] > 0:
        return 'red'
    else:
        return 'white'

In [16]:
# This function will add column with type of icon in the dataframe
def set_icon(row):
    if (row['NUMBER OF PEDESTRIANS KILLED']!=0) or (row['NUMBER OF PEDESTRIANS INJURED']!=0):
        return 'fa-male'
    elif (row['NUMBER OF CYCLIST KILLED']!=0) or (row['NUMBER OF CYCLIST INJURED']!=0):
        return 'fa-bicycle'
    elif (row['NUMBER OF MOTORIST INJURED']!=0) or (row['NUMBER OF MOTORIST KILLED']!=0):
        return 'fa-car'

In [17]:
# This function will add column with # of killed/injured persons in the dataframe
def set_info(row):
    if row['NUMBER OF PEDESTRIANS INJURED']!=0:
        return 'Pedestains injured {}'.format(row['NUMBER OF PEDESTRIANS INJURED'])
    elif row['NUMBER OF CYCLIST INJURED']!=0:
        return 'Cyclists injured {}'.format(row['NUMBER OF CYCLIST INJURED'])
    elif row['NUMBER OF MOTORIST INJURED']!=0:
        return 'Motorists injured {}'.format(row['NUMBER OF MOTORIST INJURED'])
    elif row['NUMBER OF PEDESTRIANS KILLED']!=0:
        return 'Pedestains killed {}'.format(row['NUMBER OF PEDESTRIANS KILLED'])
    elif row['NUMBER OF CYCLIST KILLED']!=0:
        return 'Cyclists killed {}'.format(row['NUMBER OF CYCLIST KILLED'])
    elif row['NUMBER OF MOTORIST KILLED']!=0:
        return 'Motorists killed {}'.format(row['NUMBER OF MOTORIST KILLED'])

In [18]:
df18_flag_man = df18_flag_man.assign(COLOR = df18_flag_man.apply(set_color, axis=1))

In [19]:
df18_flag_man = df18_flag_man.assign(INFO = df18_flag_man.apply(set_info, axis=1))

In [20]:
df18_flag_man = df18_flag_man.assign(ICON = df18_flag_man.apply(set_icon, axis=1))

NYC coordinates (LAT, LONG)

In [22]:
man_coordinates = (40.7218, -73.9998)

Now we can create map in Folium.

In [23]:
map = folium.Map(location=man_coordinates, zoom_start=12)

In [24]:
marker_cluster = MarkerCluster().add_to(map)

In [25]:
for index, row in df18_flag_man.iterrows():
    folium.Marker([row['LATITUDE'], row['LONGITUDE']], popup=row['INFO'], icon = folium.Icon(color=row['COLOR'], icon=row['ICON'], prefix='fa')).add_to(marker_cluster)

In [28]:
map

In [27]:
map.save('man_accidents1.html')